In [1]:
import pandas as pd

In [2]:
df = pd.DataFrame(
    dict(
        student_id = [1,2,2],
        first = ['ann', 'barry', 'barry'],
        last = ['ang', 'bonds', 'bonds'],
        major = [[('stats', 'Statistics'), ('biol', 'Biology')], 
                 [('stat', 'Statistics'),('math', 'Mathematics')],
                 [('stat', 'Statistics'),('math', 'Mathematics')]],
        state_abbrev = ['NC', 'QC', 'QC'],
        state_name = ['North Carolina', 'Quebec', 'Quebec'],
        country = ['USA', 'Canada', 'Canada'],
        course_id = ['BIOS101', 'BIOS101', 'BIOS102'],
        course_name = ["Frogs in medicine", 
                       "Frogs in medicine", 
                       "Medicine for frogs"]
    )
)

df

student_id  first   last                                      major  \
0           1    ann    ang     [(stats, Statistics), (biol, Biology)]   
1           2  barry  bonds  [(stat, Statistics), (math, Mathematics)]   
2           2  barry  bonds  [(stat, Statistics), (math, Mathematics)]   

  state_abbrev      state_name country course_id         course_name  
0           NC  North Carolina     USA   BIOS101   Frogs in medicine  
1           QC          Quebec  Canada   BIOS101   Frogs in medicine  
2           QC          Quebec  Canada   BIOS102  Medicine for frogs

## Normalization

- Every table should not have any 
    - duplication
    - dependencies that are not key or domain constraints

### 1NF

- Split composite entries

In [3]:
df1 = df.explode('major')
df1

student_id  first   last                major state_abbrev      state_name  \
0           1    ann    ang  (stats, Statistics)           NC  North Carolina   
0           1    ann    ang      (biol, Biology)           NC  North Carolina   
1           2  barry  bonds   (stat, Statistics)           QC          Quebec   
1           2  barry  bonds  (math, Mathematics)           QC          Quebec   
2           2  barry  bonds   (stat, Statistics)           QC          Quebec   
2           2  barry  bonds  (math, Mathematics)           QC          Quebec   

  country course_id         course_name  
0     USA   BIOS101   Frogs in medicine  
0     USA   BIOS101   Frogs in medicine  
1  Canada   BIOS101   Frogs in medicine  
1  Canada   BIOS101   Frogs in medicine  
2  Canada   BIOS102  Medicine for frogs  
2  Canada   BIOS102  Medicine for frogs

In [4]:
new_cols = ['major_id', 'major_name']
for i, c in enumerate(new_cols):
    df1[c] = df1.major.apply(lambda x: x[i])
df1 = df1.drop('major', axis=1)
df1

student_id  first   last state_abbrev      state_name country course_id  \
0           1    ann    ang           NC  North Carolina     USA   BIOS101   
0           1    ann    ang           NC  North Carolina     USA   BIOS101   
1           2  barry  bonds           QC          Quebec  Canada   BIOS101   
1           2  barry  bonds           QC          Quebec  Canada   BIOS101   
2           2  barry  bonds           QC          Quebec  Canada   BIOS102   
2           2  barry  bonds           QC          Quebec  Canada   BIOS102   

          course_name major_id   major_name  
0   Frogs in medicine    stats   Statistics  
0   Frogs in medicine     biol      Biology  
1   Frogs in medicine     stat   Statistics  
1   Frogs in medicine     math  Mathematics  
2  Medicine for frogs     stat   Statistics  
2  Medicine for frogs     math  Mathematics

### 2NF

- Break partial dependencies
    - Identify candidate PK for each row
    - If there is a composite PK, see if other columns have partial dependencies

In [5]:
df_student = df1.iloc[:, [0,1,2,3,4,5]].drop_duplicates()
df_student

student_id  first   last state_abbrev      state_name country
0           1    ann    ang           NC  North Carolina     USA
1           2  barry  bonds           QC          Quebec  Canada

In [6]:
df_course = df1.iloc[:,6:8].drop_duplicates()
df_course

course_id         course_name
0   BIOS101   Frogs in medicine
2   BIOS102  Medicine for frogs

In [7]:
df_major = df1.iloc[:,8:10].drop_duplicates()
df_major

major_id   major_name
0    stats   Statistics
0     biol      Biology
1     stat   Statistics
1     math  Mathematics

In [8]:
df_student_course = df1.iloc[:, [0, 6]].drop_duplicates()
df_student_course

student_id course_id
0           1   BIOS101
1           2   BIOS101
2           2   BIOS102

In [9]:
df_student_major = df1.iloc[:, [0, 8]].drop_duplicates()
df_student_major

student_id major_id
0           1    stats
0           1     biol
1           2     stat
1           2     math

### 3NF

- Remove transitive dependencies

In [10]:
df_student_ = df_student.iloc[:, :5].drop_duplicates()
df_student_

student_id  first   last state_abbrev      state_name
0           1    ann    ang           NC  North Carolina
1           2  barry  bonds           QC          Quebec

In [11]:
df_origin = df_student.iloc[:, 4:7].drop_duplicates()
df_origin

state_name country
0  North Carolina     USA
1          Quebec  Canada

## Final tables

In [12]:
df_student_

student_id  first   last state_abbrev      state_name
0           1    ann    ang           NC  North Carolina
1           2  barry  bonds           QC          Quebec

In [13]:
df_origin

state_name country
0  North Carolina     USA
1          Quebec  Canada

In [14]:
df_course

course_id         course_name
0   BIOS101   Frogs in medicine
2   BIOS102  Medicine for frogs

In [15]:
df_student_course

student_id course_id
0           1   BIOS101
1           2   BIOS101
2           2   BIOS102

In [16]:
df_major

major_id   major_name
0    stats   Statistics
0     biol      Biology
1     stat   Statistics
1     math  Mathematics

In [17]:
df_student_major

student_id major_id
0           1    stats
0           1     biol
1           2     stat
1           2     math

## Denormalization

In [18]:
df_student_.merge(df_origin)

student_id  first   last state_abbrev      state_name country
0           1    ann    ang           NC  North Carolina     USA
1           2  barry  bonds           QC          Quebec  Canada

In [19]:
(
    df_student_.
    merge(df_origin).
    merge(df_student_course).
    merge(df_course).
    merge(df_student_major).
    merge(df_major)
)


student_id  first   last state_abbrev      state_name country course_id  \
0           1    ann    ang           NC  North Carolina     USA   BIOS101   
1           1    ann    ang           NC  North Carolina     USA   BIOS101   
2           2  barry  bonds           QC          Quebec  Canada   BIOS101   
3           2  barry  bonds           QC          Quebec  Canada   BIOS102   
4           2  barry  bonds           QC          Quebec  Canada   BIOS101   
5           2  barry  bonds           QC          Quebec  Canada   BIOS102   

          course_name major_id   major_name  
0   Frogs in medicine    stats   Statistics  
1   Frogs in medicine     biol      Biology  
2   Frogs in medicine     stat   Statistics  
3  Medicine for frogs     stat   Statistics  
4   Frogs in medicine     math  Mathematics  
5  Medicine for frogs     math  Mathematics